In [2]:
import pandas as pd
import subprocess

In [3]:
sra_metadata1 = pd.read_csv('~/git/singlem-wdl/sra_bigquery_attributes/sra_metadata_20210922.sanitised.csv.gz', compression='gzip',header=None)
del sra_metadata1[4]
del sra_metadata1[2]
del sra_metadata1[0]
sra_metadata1[1:3]

1            3                                        5
1  SRR4010989   assay_type                                      WCS
2  SRR4010989  center_name  UNIVERSITY OF ZURICH, VETSUISSE FACULTY

In [4]:
sra_metadata = sra_metadata1
sra_metadata.columns = ['run','key','value']
print(sra_metadata.shape)
sra_metadata[1:3]

(11150617, 3)


run          key                                    value
1  SRR4010989   assay_type                                      WCS
2  SRR4010989  center_name  UNIVERSITY OF ZURICH, VETSUISSE FACULTY

In [5]:
aerobic_predictions = pd.read_csv('~/m/msingle/mess/88_sra_vs_gtdb_db2/sra_vs_gtdb_db2.query2.sorted.tsv.aerobic_predictions1.csv',sep="\t")
aerobic_predictions[1:3]

aerobe_count  anaerobe_count  aerobe_fraction
DRR001360          79.0             8.0         0.908046
DRR001455         908.0           161.0         0.849392

In [6]:
mer = pd.merge(sra_metadata, aerobic_predictions, right_index=True, left_on='run')
print(mer.shape)
mer[1:3]

(7059359, 6)


run          key                                           value  \
30  ERR2867973   assay_type                                             WGA   
31  ERR2867973  center_name  MAX PLANCK INSTITUTE FOR DEVELOPMENTAL BIOLOGY   

    aerobe_count  anaerobe_count  aerobe_fraction  
30           4.0            17.0         0.190476  
31           4.0            17.0         0.190476

In [7]:
vcs = mer.loc[:,'key'].value_counts()

In [8]:
(vcs[vcs >100000])

acc                                    173068
biosample                              173068
primary_search                         173068
assay_type                             173068
bytes                                  173068
mbases                                 173068
avgspotlen                             173068
sra_study                              173068
organism                               173068
bases                                  173068
sample_acc                             173068
instrument                             173068
center_name                            173068
platform                               173068
sample_name                            173068
experiment                             173068
libraryselection                       173068
librarysource                          173068
releasedate                            173048
bioproject                             172703
library_name                           163145
collection_date_sam.0             

In [9]:
mer.loc[mer.loc[:,'key']=='organism',:]

run       key                       value  aerobe_count  \
40        ERR2867973  organism            viral metagenome           4.0   
74        ERR2867994  organism            viral metagenome          -1.0   
108       ERR2867968  organism            viral metagenome           2.0   
177       SRR1378334  organism            viral metagenome         558.0   
216       SRR1535347  organism        human gut metagenome         772.0   
...              ...       ...                         ...           ...   
11150037  ERR3850078  organism  food production metagenome        5102.0   
11150073   DRR128697  organism       freshwater metagenome         388.0   
11150309  ERR5641982  organism         sediment metagenome           9.0   
11150345  ERR5641256  organism         sediment metagenome           2.0   
11150381  ERR5708576  organism         sediment metagenome          28.0   

          anaerobe_count  aerobe_fraction  
40                  17.0         0.190476  
74                 164.0        -0.006135  
108                166.0         0.011905  
177                  2.0         0.996429  
216              39190.0         0.019318  
...                  ...              ...  
11150037           151.0         0.971255  
11150073            45.0         0.896074  
11150309             4.0         0.692308  
11150345            -1.0         2.000000  
11150381             5.0         0.848485  

[173068 rows x 6 columns]

In [10]:
mer.loc[mer.loc[:,'aerobe_count']==-1,'aerobe_count'] = 0
mer.loc[mer.loc[:,'anaerobe_count']==-1,'anaerobe_count'] = 0
mer.loc[:,'aerobe_fraction'] = mer.loc[:,'aerobe_count'] / (mer.loc[:,'aerobe_count'] + mer.loc[:,'anaerobe_count'])

In [11]:
mer.loc[mer.loc[:,'key']=='organism',:]

run       key                       value  aerobe_count  \
40        ERR2867973  organism            viral metagenome           4.0   
74        ERR2867994  organism            viral metagenome           0.0   
108       ERR2867968  organism            viral metagenome           2.0   
177       SRR1378334  organism            viral metagenome         558.0   
216       SRR1535347  organism        human gut metagenome         772.0   
...              ...       ...                         ...           ...   
11150037  ERR3850078  organism  food production metagenome        5102.0   
11150073   DRR128697  organism       freshwater metagenome         388.0   
11150309  ERR5641982  organism         sediment metagenome           9.0   
11150345  ERR5641256  organism         sediment metagenome           2.0   
11150381  ERR5708576  organism         sediment metagenome          28.0   

          anaerobe_count  aerobe_fraction  
40                  17.0         0.190476  
74                 164.0         0.000000  
108                166.0         0.011905  
177                  2.0         0.996429  
216              39190.0         0.019318  
...                  ...              ...  
11150037           151.0         0.971255  
11150073            45.0         0.896074  
11150309             4.0         0.692308  
11150345             0.0         1.000000  
11150381             5.0         0.848485  

[173068 rows x 6 columns]

In [12]:
import plotly.express as px
from plotly.offline import iplot
import plotly.figure_factory as ff

ModuleNotFoundError: No module named 'plotly'

In [ ]:
soils = mer.loc[mer.loc[:,'value']=='soil metagenome',:]
human_gut = mer.loc[mer.loc[:,'value']=='human gut metagenome',:]
# soils.loc[:,'aerobe_fraction'].to_numpy()


In [ ]:
ff.create_distplot([soils.loc[:,'aerobe_fraction'].to_numpy()],['soil'])

In [ ]:
ff.create_distplot([human_gut.loc[:,'aerobe_fraction'].to_numpy()],['human_gut'])

In [ ]:
ff.create_distplot([mer.loc[mer.loc[:,'value']=='marine metagenome',:].loc[:,'aerobe_fraction'].to_numpy()],['marine'])

In [ ]:

ff.create_distplot([mer.loc[mer.loc[:,'value']=='sediment metagenome',:].loc[:,'aerobe_fraction'].to_numpy()],['sediment'])

In [ ]:
mer.loc[mer.loc[:,'key']=='organism','value'].value_counts()[1:30]

human metagenome                   17620
gut metagenome                     17305
metagenome                         12990
marine metagenome                   8003
soil metagenome                     4255
pig gut metagenome                  4206
human skin metagenome               4191
Homo sapiens                        4039
feces metagenome                    3749
mouse gut metagenome                3584
sediment metagenome                 3299
bacterium                           3007
wastewater metagenome               2673
terrestrial metagenome              1625
air metagenome                      1503
freshwater metagenome               1470
oral metagenome                     1302
Arabidopsis thaliana                1261
human oral metagenome               1253
aquatic metagenome                   833
seawater metagenome                  793
synthetic metagenome                 777
bovine gut metagenome                771
human nasopharyngeal metagenome      757
bioreactor metag

In [13]:
mer.to_csv('aerobic_sra_for_R.csv')